# Fine-Tuning BERT as a `RewardModel`

1. First, intall `transformers`, `tlr`, and `codecarbon`.

In [1]:
%pip install transformers
%pip install trl
%pip install codecarbon

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.2/7.2 MB 52.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 236.8/236.8 kB 23.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.8/7.8 MB 92.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.3/1.3 MB 71.2 MB/s eta 0:00:00


2. Downloas the `reward-aira-dataset-comparisons` from the Hub.

In [2]:
from datasets import load_dataset

dataset = load_dataset("nicholasKluge/reward-aira-dataset", split="portuguese")

print("Dataset loaded.")

Found cached dataset parquet (C:/Users/CWLINK/.cache/huggingface/datasets/nicholasKluge___parquet/nicholasKluge--reward-aira-dataset-9a1556f180412706/0.0.0/2a3b91fbd88a2c90d1dbbb32b460cf621d31bd5b05b934492fdef7d8d6f236ec)


Dataset loaded.


3. Download your base model for fine-tuning. Here he are using `bert-base-cased` for the English reward model and `bert-base-portuguese-cased` for the Portuguse version.

In [ ]:
from transformers import AutoModelForSequenceClassification, AutoTokenizer
import torch

model_name = "bert-base-cased" # "neuralmind/bert-base-portuguese-cased" bert-base-cased

model = AutoModelForSequenceClassification.from_pretrained(model_name, num_labels=1)
tokenizer = AutoTokenizer.from_pretrained(model_name)

if tokenizer.pad_token is None:
    tokenizer.pad_token = tokenizer.eos_token
    model.config.pad_token_id = model.config.eos_token_id

print(f"Model ({model_name}) ready.")

Some weights of the model checkpoint at bert-base-cased were not used when initializing BertForSequenceClassification: ['cls.predictions.transform.dense.weight', 'cls.seq_relationship.bias', 'cls.predictions.transform.LayerNorm.weight', 'cls.predictions.bias', 'cls.seq_relationship.weight', 'cls.predictions.transform.LayerNorm.bias', 'cls.predictions.transform.dense.bias']
- This IS expected if you are initializing BertForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of BertForSequenceClassification were not initialized from the model checkpoint at bert-base-cased and are newly initi

Model (bert-base-cased) ready.


4. Preprocess the dataset to be compatible with the `RewardTrainer` from `tlr`.

In [ ]:
def preprocess(examples):
    kwargs = {"padding": "max_length", "truncation": True, "max_length": 350, "return_tensors": "pt"}

    prompt_plus_chosen_response = examples["instruction"] + "[SEP]" + examples["chosen_response"]
    prompt_plus_rejected_response = examples["instruction"] + "[SEP]" + examples["rejected_response"]

    # Then tokenize these modified fields.
    tokens_chosen = tokenizer.encode_plus(prompt_plus_chosen_response, **kwargs)
    tokens_rejected = tokenizer.encode_plus(prompt_plus_rejected_response, **kwargs)

    return {
        "input_ids_chosen": tokens_chosen["input_ids"][0], "attention_mask_chosen": tokens_chosen["attention_mask"][0],
        "input_ids_rejected": tokens_rejected["input_ids"][0], "attention_mask_rejected": tokens_rejected["attention_mask"][0]
    }

formatted_dataset = dataset.map(preprocess)
formatted_dataset = formatted_dataset.train_test_split()

Map:   0%|          | 0/34234 [00:00<?, ? examples/s]

5. Train your model while tracking the CO2 emissions. 🌱

In [ ]:
from transformers import TrainingArguments
from codecarbon import EmissionsTracker
from trl import RewardTrainer

tracker = EmissionsTracker(
    project_name="RewardModel_emissions",
    log_level="critical",
    output_dir=f"/content/drive/MyDrive/Colab Notebooks/RewardModel",
    output_file="RewardModel_emissions.csv",
)

training_args = TrainingArguments(
    output_dir="/content/drive/MyDrive/Colab Notebooks/RewardModel",
    per_device_train_batch_size=42,
    per_device_eval_batch_size=42,
    evaluation_strategy="steps",
    logging_steps=200,
    num_train_epochs=5,
    learning_rate = 5e-5,

)

trainer = RewardTrainer(
    model=model,
    args=training_args,
    tokenizer=tokenizer,
    train_dataset=formatted_dataset["train"],
    eval_dataset=formatted_dataset["test"],
)

tracker.start()
trainer.train()
tracker.stop()

Using the `WANDB_DISABLED` environment variable is deprecated and will be removed in v5. Use the --report_to flag to control the integrations used for logging result (for instance --report_to none).
/usr/local/lib/python3.10/dist-packages/trl/trainer/reward_trainer.py:125: UserWarning: When using RewardDataCollatorWithPadding, you should set `max_length` in the RewardTrainer's init it will be set to `512` by default, but you should do it yourself in the future.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/trl/trainer/reward_trainer.py:136: UserWarning: When using RewardDataCollatorWithPadding, you should set `remove_unused_columns=False` in your TrainingArguments we have set it for you, but you should do it yourself in the future.
  warnings.warn(
[codecarbon INFO @ 13:43:43] [setup] RAM Tracking...
[codecarbon INFO @ 13:43:43] [setup] GPU Tracking...
[codecarbon INFO @ 13:43:43] Tracking Nvidia GPU via pynvml
[codecarbon INFO @ 13:43:43] [setup] CPU Tracking...
[codecarbon

[codecarbon INFO @ 13:43:59] Energy consumed for RAM : 0.000130 kWh. RAM Power : 31.30528450012207 W
[codecarbon INFO @ 13:43:59] Energy consumed for all GPUs : 0.001082 kWh. Total GPU Power : 259.618 W
[codecarbon INFO @ 13:43:59] Energy consumed for all CPUs : 0.000177 kWh. Total CPU Power : 42.5 W
[codecarbon INFO @ 13:43:59] 0.001390 kWh of electricity used since the beginning.
[codecarbon INFO @ 13:44:00] Energy consumed for RAM : 0.000130 kWh. RAM Power : 31.30528450012207 W
[codecarbon INFO @ 13:44:00] Energy consumed for all GPUs : 0.001343 kWh. Total GPU Power : 322.313 W
[codecarbon INFO @ 13:44:00] Energy consumed for all CPUs : 0.000177 kWh. Total CPU Power : 42.5 W
[codecarbon INFO @ 13:44:00] 0.001651 kWh of electricity used since the beginning.
[codecarbon INFO @ 13:44:14] Energy consumed for RAM : 0.000261 kWh. RAM Power : 31.30528450012207 W
[codecarbon INFO @ 13:44:14] Energy consumed for all GPUs : 0.002175 kWh. Total GPU Power : 262.56 W
[codecarbon INFO @ 13:44:14]

0.17002787857474966

6. Test your RewardModel!

In [1]:
from transformers import AutoTokenizer, AutoModelForSequenceClassification
import torch

device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

tokenizer = AutoTokenizer.from_pretrained("nicholasKluge/RewardModelPT")
rewardModel = AutoModelForSequenceClassification.from_pretrained("nicholasKluge/RewardModelPT")

rewardModel.eval()
rewardModel.to(device)

# Define the question and response
prompt = "Por que a ética da IA é importante?"
response_good = "O campo da ética da IA se aprofunda nas intrincadas considerações éticas que surgem com relação aos sistemas de IA. Isso inclui o papel da humanidade na criação e implantação desses sistemas, bem como a conduta das próprias máquinas. Em termos gerais, a ética da IA pode ser dividida em duas categorias principais: preocupações com a moralidade das ações humanas em relação à criação e ao uso da IA e preocupações com as implicações morais do comportamento da máquina."
response_bad = "Quem se importa com a ética da IA? É apenas um monte de reclamações sobre os humanos que criam e usam IA e reclamam do que as máquinas fazem."

# Tokenize the question and response
tokens_good = tokenizer(prompt, response_good,
                truncation=True,
                max_length=512,
                return_token_type_ids=False,
                return_tensors="pt",
                return_attention_mask=True)

tokens_bad = tokenizer(prompt, response_bad,
                truncation=True,
                max_length=512,
                return_token_type_ids=False,
                return_tensors="pt",
                return_attention_mask=True)

tokens_good.to(device)
tokens_bad.to(device)

score_good = rewardModel(**tokens_good)[0].item()
score_bad = rewardModel(**tokens_bad)[0].item()

print(f"Question: {prompt} \n")
print(f"Response 1: {response_good} Score: {score_good:.3f}")
print(f"Response 2: {response_bad} Score: {score_bad:.3f}")

Downloading:   0%|          | 0.00/395 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/210k [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/678k [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/125 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/953 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/436M [00:00<?, ?B/s]

Question: Por que a ética da IA é importante? 

Response 1: O campo da ética da IA se aprofunda nas intrincadas considerações éticas que surgem com relação aos sistemas de IA. Isso inclui o papel da humanidade na criação e implantação desses sistemas, bem como a conduta das próprias máquinas. Em termos gerais, a ética da IA pode ser dividida em duas categorias principais: preocupações com a moralidade das ações humanas em relação à criação e ao uso da IA e preocupações com as implicações morais do comportamento da máquina. Score: 10.622
Response 2: Quem se importa com a ética da IA? É apenas um monte de reclamações sobre os humanos que criam e usam IA e reclamam do que as máquinas fazem. Score: -11.609


Done! 🤗